In [1]:
import numpy as np
import math
from tensorflow.examples.tutorials.mnist import input_data

# Neural network has four layers
# The input layer has 784 nodes
# The two hidden layers each have 5 nodes
# The output layer has 10 nodes
num_layer = 4
num_node = [784,5,5,10]
num_output_node = 10

# 30000 training sets are used
# 10000 test sets are used
# Can be adjusted
Ntrain = 30000
Ntest = 10000

# Sigmoid Function
def g(X):
    return 1/(1 + np.exp(-X))

# Forwardpropagation
def h(W,X):
    a = X
    for l in range(num_layer - 1):
        a = np.insert(a,0,1)
        z = np.dot(a,W[l])
        a = g(z)
    return a      

# Cost Function
def J(y, W, X, Lambda):
    cost = 0
    for i in range(Ntrain):
        H = h(W,X[i])
        for k in range(num_output_node):            
            cost = cost + y[i][k] * math.log(H[k]) + (1-y[i][k]) * math.log(1-H[k])
    regularization = 0
    for l in range(num_layer - 1):
        for i in range(num_node[l]):
            for j in range(num_node[l+1]):
                regularization = regularization + W[l][i+1][j] ** 2
    return (-1/Ntrain * cost + Lambda / (2*Ntrain) * regularization)

# Backpropagation - confirmed to be correct
# Algorithm based on https://www.coursera.org/learn/machine-learning/lecture/1z9WW/backpropagation-algorithm
# Returns D, the value of the gradient
def BackPropagation(y, W, X, Lambda):
    delta = np.empty(num_layer-1, dtype = object)
    for l in range(num_layer - 1):
        delta[l] = np.zeros((num_node[l]+1,num_node[l+1]))
    for i in range(Ntrain):
        A = np.empty(num_layer-1, dtype = object)
        a = X[i]
        for l in range(num_layer - 1):
            A[l] = a
            a = np.insert(a,0,1)
            z = np.dot(a,W[l])
            a = g(z)
        diff = a - y[i]
        delta[num_layer-2] = delta[num_layer-2] + np.outer(np.insert(A[num_layer-2],0,1),diff)
        for l in range(num_layer-2):
            index = num_layer-2-l
            diff = np.multiply(np.dot(np.array([W[index][k+1] for k in range(num_node[index])]), diff), np.multiply(A[index], 1-A[index])) 
            delta[index-1] = delta[index-1] + np.outer(np.insert(A[index-1],0,1),diff)
    D = np.empty(num_layer-1, dtype = object)
    for l in range(num_layer - 1):
        D[l] = np.zeros((num_node[l]+1,num_node[l+1]))
    for l in range(num_layer-1):
        for i in range(num_node[l]+1):
            if i == 0:
                for j in range(num_node[l+1]):
                    D[l][i][j] = 1/Ntrain * delta[l][i][j]
            else:
                for j in range(num_node[l+1]):
                    D[l][i][j] = 1/Ntrain * (delta[l][i][j] + Lambda * W[l][i][j])
    return D

# Neural network - this is where the learning/adjusting of weights occur
# W is the weights
# learn is the learning rate
# iterations is the number of iterations we pass over the training set
# Lambda is the regularization parameter
def NeuralNetwork(y, X, learn, iterations, Lambda):

    W = np.empty(num_layer-1, dtype = object)
    for l in range(num_layer - 1):
        W[l] = np.random.rand(num_node[l]+1,num_node[l+1])/100
    for k in range(iterations):
        print(J(y, W, X, Lambda))
        D = BackPropagation(y, W, X, Lambda)
        for l in range(num_layer-1):
            W[l] = W[l] - learn * D[l]
    print(J(y, W, X, Lambda))
    return W

mnist = input_data.read_data_sets("MNIST_data/", one_hot=True)

# Training data, read from MNIST
inputpix = []
output = []

for i in range(Ntrain):
    inputpix.append(2 * np.array(mnist.train.images[i]) - 1)
    output.append(np.array(mnist.train.labels[i]))

np.savetxt('input.txt', inputpix, delimiter=' ')
np.savetxt('output.txt', output, delimiter=' ')

# Train the weights
finalweights = NeuralNetwork(output, inputpix, 2, 5, 1)

# Test data
inputtestpix = []
outputtest = []

for i in range(Ntest):
    inputtestpix.append(2 * np.array(mnist.test.images[i]) - 1)
    outputtest.append(np.array(mnist.test.labels[i]))

np.savetxt('inputtest.txt', inputtestpix, delimiter=' ')
np.savetxt('outputtest.txt', outputtest, delimiter=' ')

# Determine the accuracy of the training data
count = 0
for i in range(Ntrain):
    H = h(finalweights,inputpix[i])
    print(H)
    for j in range(num_output_node):
        if H[j] == np.amax(H) and output[i][j] == 1:
            count = count + 1
print(count/Ntrain)

# Determine the accuracy of the test data
count = 0
for i in range(Ntest):
    H = h(finalweights,inputtestpix[i])
    print(H)
    for j in range(num_output_node):
        if H[j] == np.amax(H) and outputtest[i][j] == 1:
            count = count + 1
print(count/Ntest)

D:\anaconda\lib\site-packages\h5py\__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters
W1105 18:07:07.490120  6824 deprecation.py:323] From <ipython-input-1-78afbab10bf4>:98: read_data_sets (from tensorflow.contrib.learn.python.learn.datasets.mnist) is deprecated and will be removed in a future version.
Instructions for updating:
Please use alternatives such as official/mnist/dataset.py from tensorflow/models.
W1105 18:07:07.490120  6824 deprecation.py:323] From D:\anaconda\lib\site-packages\tensorflow\contrib\learn\python\learn\datasets\mnist.py:260: maybe_download (from tensorflow.contrib.learn.python.learn.datasets.base) is deprecated and will be removed in a future version.
Instructions for updating:
Please write your own downloading logic.
W1105 18:07:07.504082  6824 deprecati

Successfully downloaded train-images-idx3-ubyte.gz 9912422 bytes.
Extracting MNIST_data/train-images-idx3-ubyte.gz


W1105 18:07:09.961852  6824 deprecation.py:323] From D:\anaconda\lib\site-packages\tensorflow\contrib\learn\python\learn\datasets\mnist.py:267: extract_labels (from tensorflow.contrib.learn.python.learn.datasets.mnist) is deprecated and will be removed in a future version.
Instructions for updating:
Please use tf.data to implement this functionality.
W1105 18:07:09.965842  6824 deprecation.py:323] From D:\anaconda\lib\site-packages\tensorflow\contrib\learn\python\learn\datasets\mnist.py:110: dense_to_one_hot (from tensorflow.contrib.learn.python.learn.datasets.mnist) is deprecated and will be removed in a future version.
Instructions for updating:
Please use tf.one_hot on tensors.


Successfully downloaded train-labels-idx1-ubyte.gz 28881 bytes.
Extracting MNIST_data/train-labels-idx1-ubyte.gz
Successfully downloaded t10k-images-idx3-ubyte.gz 1648877 bytes.
Extracting MNIST_data/t10k-images-idx3-ubyte.gz


W1105 18:07:10.516673  6824 deprecation.py:323] From D:\anaconda\lib\site-packages\tensorflow\contrib\learn\python\learn\datasets\mnist.py:290: DataSet.__init__ (from tensorflow.contrib.learn.python.learn.datasets.mnist) is deprecated and will be removed in a future version.
Instructions for updating:
Please use alternatives such as official/mnist/dataset.py from tensorflow/models.


...

[0.09970293 0.11459489 0.0994049  0.10356728 0.097241   0.09253421
 0.09994139 0.1035215  0.09834916 0.10190142]
[0.09984332 0.11474254 0.09954564 0.10371033 0.09738033 0.09267071
 0.10008198 0.10366407 0.09848893 0.10204336]
[0.09963879 0.11452743 0.09934058 0.1035019  0.09717734 0.09247183
 0.09987716 0.10345636 0.09828529 0.10183656]
[0.09977249 0.11466805 0.09947463 0.10363816 0.09731004 0.09260184
 0.10001105 0.10359214 0.09841841 0.10197175]
[0.09979467 0.11469137 0.09949688 0.10366077 0.09733204 0.09262342
 0.10003326 0.10361466 0.09844049 0.10199418]
[0.09980423 0.11470143 0.09950646 0.10367051 0.09734153 0.09263271
 0.10004284 0.10362437 0.09845001 0.10200385]
[0.09977761 0.11467343 0.09947977 0.10364338 0.09731511 0.09260682
 0.10001617 0.10359734 0.09842351 0.10197693]
[0.09979119 0.11468771 0.09949339 0.10365722 0.09732859 0.09262003
 0.10002978 0.10361113 0.09843703 0.10199067]
[0.0998027  0.11469982 0.09950493 0.10366895 0.09734002 0.09263122
 0.1000413  0.10362282 0.0984

[0.09983822 0.11473717 0.09954054 0.10370514 0.09737527 0.09266576
 0.10007687 0.10365889 0.09848385 0.10203821]
[0.09979287 0.11468948 0.09949507 0.10365893 0.09733026 0.09262166
 0.10003146 0.10361284 0.0984387  0.10199237]
[0.09979543 0.11469217 0.09949763 0.10366154 0.0973328  0.09262415
 0.10003402 0.10361544 0.09844125 0.10199495]
[0.09973905 0.11463289 0.09944111 0.10360408 0.09727685 0.09256932
 0.09997757 0.10355819 0.09838512 0.10193794]
[0.09980133 0.11469838 0.09950355 0.10366755 0.09733865 0.09262988
 0.10003993 0.10362143 0.09844713 0.10200092]
[0.09979576 0.11469252 0.09949796 0.10366187 0.09733313 0.09262447
 0.10003436 0.10361577 0.09844158 0.10199528]
[0.09986109 0.11476123 0.09956347 0.10372845 0.09739797 0.09268799
 0.10009978 0.10368212 0.09850662 0.10206134]
[0.09983759 0.11473651 0.0995399  0.1037045  0.09737464 0.09266514
 0.10007624 0.10365825 0.09848322 0.10203757]
[0.09989021 0.11479185 0.09959266 0.10375812 0.09742687 0.09271631
 0.10012894 0.1037117  0.0985

[0.09987044 0.11477105 0.09957284 0.10373797 0.09740724 0.09269708
 0.10010914 0.10369161 0.09851593 0.10207079]
[0.09975854 0.11465338 0.09946065 0.10362395 0.09729619 0.09258828
 0.09999708 0.10357798 0.09840453 0.10195765]
[0.09974874 0.11464307 0.09945082 0.10361395 0.09728646 0.09257874
 0.09998726 0.10356802 0.09839476 0.10194774]
[0.09985404 0.11475381 0.0995564  0.10372126 0.09739097 0.09268114
 0.10009271 0.10367496 0.09849961 0.10205421]
[0.09982509 0.11472336 0.09952738 0.10369176 0.09736223 0.09265299
 0.10006372 0.10364556 0.09847078 0.10202494]
[0.09989032 0.11479197 0.09959278 0.10375824 0.09742698 0.09271642
 0.10012905 0.10371181 0.09853573 0.10209089]
[0.09983056 0.11472912 0.09953286 0.10369734 0.09736767 0.09265831
 0.10006921 0.10365111 0.09847623 0.10203047]
[0.0998708  0.11477143 0.0995732  0.10373834 0.0974076  0.09269743
 0.1001095  0.10369198 0.09851629 0.10207115]
[0.09985541 0.11475526 0.09955778 0.10372266 0.09739233 0.09268248
 0.10009409 0.10367636 0.0985

[0.09980995 0.11470744 0.09951218 0.10367633 0.0973472  0.09263826
 0.10004856 0.10363018 0.0984557  0.10200963]
[0.09986412 0.11476441 0.0995665  0.10373153 0.09740097 0.09269094
 0.10010281 0.1036852  0.09850964 0.1020644 ]
[0.09981636 0.11471419 0.09951862 0.10368287 0.09735357 0.0926445
 0.10005498 0.1036367  0.09846209 0.10201612]
[0.09986522 0.11476557 0.09956761 0.10373266 0.09740207 0.09269202
 0.10010392 0.10368632 0.09851074 0.10206552]
[0.09983628 0.11473513 0.09953859 0.10370316 0.09737334 0.09266386
 0.10007493 0.10365692 0.09848192 0.10203625]
[0.09984728 0.1147467  0.09954962 0.10371437 0.09738426 0.09267456
 0.10008594 0.10366809 0.09849287 0.10204737]
[0.09986824 0.11476874 0.09957063 0.10373573 0.09740506 0.09269494
 0.10010693 0.10368938 0.09851374 0.10206856]
[0.09987918 0.11478025 0.0995816  0.10374688 0.09741592 0.09270558
 0.10011789 0.10370049 0.09852463 0.10207963]
[0.0997774  0.11467322 0.09947956 0.10364316 0.09731491 0.09260662
 0.10001597 0.10359713 0.09842

 0.10007157 0.10365351 0.09847857 0.10203285]
[0.09985523 0.11475507 0.09955759 0.10372248 0.09739215 0.0926823
 0.10009391 0.10367617 0.09850079 0.10205541]
[0.099814   0.1147117  0.09951625 0.10368045 0.09735123 0.0926422
 0.10005262 0.1036343  0.09845973 0.10201372]
[0.09978891 0.11468531 0.0994911  0.10365489 0.09732633 0.09261781
 0.10002749 0.10360881 0.09843476 0.10198835]
[0.09986382 0.11476409 0.0995662  0.10373123 0.09740067 0.09269065
 0.10010251 0.10368489 0.09850934 0.1020641 ]
[0.09988501 0.11478638 0.09958745 0.10375282 0.09742171 0.09271126
 0.10012373 0.10370641 0.09853044 0.10208552]
[0.09982692 0.11472529 0.09952921 0.10369363 0.09736405 0.09265477
 0.10006555 0.10364741 0.0984726  0.10202679]
[0.09985437 0.11475416 0.09955673 0.1037216  0.0973913  0.09268146
 0.10009305 0.1036753  0.09849993 0.10205454]
[0.09983001 0.11472854 0.0995323  0.10369677 0.09736712 0.09265777
 0.10006865 0.10365055 0.09847568 0.10202991]
[0.09986691 0.11476735 0.0995693  0.10373438 0.09740